# Time-Harmonic Elastic Wave Problem  - Galerkin method

$$
\DeclareMathOperator{\Div}{div}
   \Div (\sigma (u) ) - \rho \omega^2 u = 0 \quad\mbox{in} \quad\Omega,\\
   u = g\quad\mbox{on}\quad \partial \Omega,
$$
where

$$
\DeclareMathOperator{\Div}{div}
\sigma (u) = 2\mu \,\varepsilon(u) + \lambda \,div(\varepsilon(u))\,I\\
$$

and

$$
\DeclareMathOperator{\Div}{div}
\varepsilon(u) = \nabla^s u = \frac{(\nabla u + (\nabla u)^T)}{2}.\\
$$



## Variational Formulation

$$
\DeclareMathOperator{\Div}{div}
a(u, v ) = 
   \int_{\Omega} (\sigma (u) : \varepsilon(v) - \rho \omega^2 u\cdot v)
$$

and

$$
\DeclareMathOperator{\Div}{div}
f(v) = 
  0.
$$




In [1]:
import netgen.gui
import numpy as np
from math import pi
from netgen.geom2d import unit_square
from ngsolve import *
mesh = Mesh(unit_square.GenerateMesh(maxh=0.05))

In [2]:
order=4
condense = False

# Data
# Wavenumber & source
omega = 12
rho = 1
E, nu = 1, 0.3
mu  = E / 2 / (1+nu)
lamb = E * nu / ((1+nu)*(1-2*nu))

theta = 30
theta = theta * (pi/180)

kp = omega * (sqrt(rho/(2*mu + lamb)))
ks = omega * (sqrt(rho/mu))

coef1 = CoefficientFunction( (cos(theta),sin(theta)) )
coef2 = CoefficientFunction( (-sin(theta),cos(theta)) )

r_source = coef1 * exp((1j*kp)*(x*(cos(theta)) + y*(sin(theta)))) +\
           coef2 * exp((1j*ks)*(x*(cos(theta)) + y*(sin(theta))))

# Draw(r_source[1], mesh, 'r_source')

# Case 1

In [3]:

fes = VectorH1(mesh, order=order, complex=True)

u = fes.TrialFunction()
v = fes.TestFunction()

def epsilon(u):
    return 0.5*(grad(u) + grad(u).trans)

def sigma(u):
    return lamb*div(u)*Id(mesh.dim) + 2*mu*epsilon(u)


force = CoefficientFunction( (0,0) )

a = BilinearForm(fes, condense=condense)
a += (  InnerProduct(sigma(u), epsilon(v)) -rho * omega**2 * InnerProduct(u, v)) * dx

f = LinearForm(fes)
f += SymbolicLFI(force*v)
f += InnerProduct(r_source,v.Trace()) * ds

a.Assemble()
f.Assemble()

ud = GridFunction(fes, name="ud")

print ("A non-zero elements:", a.mat.nze)
print(ud.Operators())

grid = GridFunction(fes, name='grid')
grid.vec.data = a.mat.Inverse(fes.FreeDofs()) * f.vec

A non-zero elements: 704708
['div', 'divfree_reconstruction', 'Grad', 'dual']


In [4]:
gfu = GridFunction(fes)

if not condense:
    inv = a.mat.Inverse(fes.FreeDofs(), "umfpack")
    gfu.vec.data = inv * f.vec
else:
    f.vec.data += a.harmonic_extension_trans * f.vec 
    
    inv = a.mat.Inverse(fes.FreeDofs(True), "umfpack")
    gfu.vec.data = inv * f.vec
    
    gfu.vec.data += a.harmonic_extension * gfu.vec
    gfu.vec.data += a.inner_solve * f.vec

In [5]:
Draw (gfu.components[0], mesh, "u")

In [6]:
u_exact = CoefficientFunction(r_source)
u = CoefficientFunction(gfu)

#Error analysis
print ("Displacement L2-error:", sqrt (Integrate ( (u-u_exact)*(u-u_exact), mesh)))


Pres L2-error: (0.5369369814736593+0.3579197970433251j)


## Case 2



# Time-Harmonic Elastic Wave Problem  - Pointwise Source


$$
\DeclareMathOperator{\Div}{div}
   \Div (\sigma (u) ) - \rho \omega^2 u = \delta I \quad\mbox{in} \quad\Omega,\\
   \sigma (u)n + i A u = r\quad\mbox{on}\quad \partial \Omega,
$$

where

$$
\DeclareMathOperator{\Div}{div}
\sigma (u) = 2\mu \,\varepsilon(u) + \lambda \,\Div(\varepsilon(u))\,I\\
$$

and

$$
\DeclareMathOperator{\Div}{div}
\varepsilon(u) = \nabla^s u = \frac{(\nabla u + (\nabla u)^T)}{2}\\
$$


# How can I create a pointwise source as   $f(x) = \delta(x) I$?